# Travaux pratiques, semaine 13. 
## Matrices de Hessenberg et Algorithme QR.


In [ ]:
# Chargement des bibliothèques
import numpy as np    # Pour faire du calcul scientifique, pas besoin de graphiques pour cette séance.
import matplotlib.pyplot as plt   # Pour illustrer les résultats à l’aide de graphiques

## Exercice 1 (Matrice de Hessenberg similaire à une matrice $A$)
Une matrice est dite de [Hessenberg](https://en.wikipedia.org/wiki/Hessenberg_matrix) si toutes les diagonales inférieures, à part la diagonale principale et celle située juste en-dessous, sont nulles. L’objectif est de coder un [algorithme à base de matrices de Householder](https://en.wikipedia.org/wiki/Hessenberg_matrix#Householder_transformations) pour écrire toute matrice $A$ sous la forme $QHQ^{\top}$, où $H$ est une matrice de Hessenberg et $Q$ une matrice orthogonale.

Étant donné un vecteur $\mathbf{v}$ de $\mathbb{R}^n$, la transformation de Householder associée au vecteur $\mathbf{v}$ est la symétrie orthogonale, ou réflexion, par rapport à l'hyperplan orthogonal à $\mathbf{v}$. Sa matrice $H_{\mathbf{v}}$ (dans la base canonique) est donnée par
$$
H_{\mathbf{v}}=I_n-\frac{2}{⟨\mathbf{v},\mathbf{v}⟩}\mathbf{v}\mathbf{v}^\top.
$$

**1.** Écrire une fonction `multGaucheHouseholder` ayant comme argument d'entrée un vecteur $\mathbf{v}$ et une matrice $A$ et renvoyant la matrice $H_{\mathbf{v}}A$, et une fonction `conjugueHouseholder` renvoyant $H_{\mathbf{v}}AH_{\mathbf{v}}$.

Vérifier en l’appliquant plusieurs fois (avec des $\mathbf{v}$ tirés au hasard) à la matrice identité que l’on obtient bien une matrice orthogonale pour la première fonction, et que l’on reste bien sur l’identité avec la deuxième.

**2.** L’algorithme de transformation d’une matrice $n×n$ en une matrice de Hessenberg consiste à conjuguer successivement par des matrices $H_{\mathbf{v_i}}$ pour $1⩽i⩽n-1$, où $\mathbf{v_i}$ a les $i$ premières coordonnées nulles. Ainsi à chaque étape, la multiplication à gauche par $H_{\mathbf{v_i}}$ permet de rendre nulles les coordonnées voulues dans la colonne $i$, et la multiplication à droite n’affecte pas la colonne $i$.

On pose $A^{(0)}=A$, $Q^{(0)}=I_n$ et pour $i⩾1$, $A^{(i)}=H_{\mathbf{v_i}}A^{(i-1)}H_{\mathbf{v_i}}$ et $Q^{(i)}=H_{\mathbf{v_i}}Q^{(i-1)}$ (de sorte que l’on a toujours $Q^{(i)}A(Q^{(i)})^{\top}$), où $\mathbf{v_i}$ est défini de la manière suivante : si la colonne $i$ de $A^{(i-1)}$ est de la forme $\begin{pmatrix}\mathbf{u}_i\\ d_{i+1} \\ \mathbf{x}_i\end{pmatrix}$, où $u$ est de taille $i$, $d_{i+1}$ est le coefficient en-dessous de la diagonale et $x$ de taille $n-i-1$, on pose $\mathbf{v}_i=\begin{pmatrix}0\\ α_i+ε_i d_{i+1} \\ ε_i\mathbf{x}_i\end{pmatrix}$, avec $α_i=\|\binom{d_{i+1}}{\mathbf{x}_i}\|$, et $ε_i=±1$ du signe correspondant au signe de $d_{i+1}$ (on prend $ε_i=-1$ si $d_{i+1}=0$) et où $\|…\|$ est la norme euclidienne (du vecteur de taille $n-i$).

Coder une fonction `Hessenberg` prenant en entrée une matrice $A$ et renvoyant $B=A^{(n-1)}$ et $Q=Q^{(n-1)}$. Vérifier sur un exemple avec $A$ tirée aléatoirement que $B$ est bien de Hessenberg, que $Q$ est bien orthogonale, et que $B=QAQ^{\top}$. 

# Exercice 2 (Algorithme QR pour une matrice de Hessenberg).

Pour une matrice de Hessenberg $B$, on peut faire sa décomposition QR en moins d’étapes que si elle avait tous ses coefficients non-nuls. On peut utiliser de nouveau des matrices de Householder (comme dans le TP9, avec cette fois-ci seulement deux éléments non nuls dans $\mathbf{v}_i$, on pourrait donc optimiser le code du TP9 pour ne modifier à chaque fois que les deux lignes / colonnes concernées), ou des rotations de Givens (cf. Exercice bonus du TP9). On donne ici le code à base des rotations de Givens, que l’on pourra utiliser comme « boîte noire ».

**1.** Utiliser ce code sur une matrice de Hessenberg de votre choix (par exemple obtenue avec l’exercice précédent), et vérifier qu’il fonctionne. Observer que la matrice $Q$ obtenue est alors également une matrice de Hessenberg.


In [ ]:
def QRGivensHessenberg(B):
    n,_=B.shape
    Q=np.eye(n)
    R=B.astype(float) # on s’assure que c’est bien des flottants
    for i in range(n-1):
        r=np.linalg.norm(R[i:i+2,i])
        c,s=R[i,i]/r,-R[i+1,i]/r # cosinus, sinus
        G=np.array([[c,-s],[s,c]])
        # On multiplie R à gauche par la rotation (opération sur les lignes i i+1 seulement)
        R[i:i+2,:]= G @ (R[i:i+2,:])
        # On multiplie Q à droite par la rotation inverse (opération sur les colonnes i i+1 seulement)
        Q[:,i:i+2]= Q[:,i:i+2] @ G.T
    return Q,R

L’algorithme QR (qui se base sur la décomposition QR) est un algorithme itératif ayant pour but d’obtenir les valeurs propres d’une matrice $B$.

L’idée est la suivante : on pose $B^{(0)}=B$. À l’étape $k⩾0$, on écrit la décomposition QR : $B^{(k)}=Q^{(k)}R^{(k)}$. Et on pose alors $B^{(k+1)}=R^{(k)}Q^{(k)}$. D’après ce que l’on a observé précédemment, si $R^{(k)}$ est triangulaire supérieure et $Q^{(k)}$ une matrice de Hessenberg, alors $B^{(k+1)}$ est encore une matrice de Hessenberg, donc on peut réitérer avec le même algorithme de décomposition QR.

On observe également que $B^{(k+1)}=R^{(k)}Q^{(k)}=(Q^{(k)})^{\top}B^{(k)}Q^{(k)}$, de sorte que $B^{(k+1)}$ est orthogonalement semblable à $B^{(k)}$, et par récurrence à $B$ : on a $B=P^{(k)}B^{(k+1)}(P^{(k)})^{\top}$ avec $P{(k)}=Q^{(0)}…Q^{(k)}$.

Sous certaines conditions (en particulier si la matrice est diagonalisable, mais il faut d’autres conditions également), la matrice $B^{(k)}$ converge vers une matrice triangulaire supérieure, qui est donc semblable à $B$, et comporte donc les valeurs propres de $B$ sur sa diagonale.

**2.** Écrire une fonction prenant en entrée une matrice de Hessenberg $B$, une tolérance $δ$, un nombre maximal d’itération, et renvoie l’approximation de la limite $B^{(k+1)}$, la matrice de similitude $P^{(k)}$, ainsi que la suite des incréments $‖B^{(k+1)}-B^{(k)}‖$, pour observer la vitesse de convergence. On prendra comme critère d’arrêt que $‖B^{(k+1)}-B^{(k)}‖<δ‖B‖$. 

Essayer cette fonction sur la matrice tridiagonale ayant des $3$ sur la diagonale principale et des $-1$ sur les deux autres. Cette matrice étant symétrique, on obtient en fait que toutes les itérées $B^{(k)}$ sont symétriques, donc si elles convergent vers une matrice triangulaire supérieure, elle sera en fait diagonale, et la matrice de similitude donnera les vecteurs propres. 

Afficher le graphe des 4 vecteurs propres (vu comme fonctions de leur coordonnées) associés aux 4 valeurs propres de plus petit module.

**3.** Observer la vitesse de convergence sur l’exemple précédent, et comparer la vitesse de convergence en changeant les $3$ sur la diagonale par $1$, $2$ ou $10$.

**4.** Utiliser la fonction de la question **2.** et l’exercice $1$ pour essayer de déterminer les valeurs propres d’une matrice carrée quelconque. On pourra d’abord se fixer (ou tirer aléatoirement) des valeurs propres sur une diagonale $D$, une matrice $P$ tirée aléatoirement et prendre $A=PDP^{-1}$.

Puis on pourra tirer aléatoirement $A$ et observer ce qui se passe lorsque $A$ n’est pas diagonalisable (parce que ses valeurs propres sont complexes par exemple).